In [1]:
# Code to accompany the paper "Constructions in combinatorics via neural networks and LP solvers" by A Z Wagner
# Code for conjecture 2.1, without the use of numba 
#
# Please keep in mind that I am far from being an expert in reinforcement learning. 
# If you know what you are doing, you might be better off writing your own code.
#
# This code works on tensorflow version 1.14.0 and python version 3.6.3
# It mysteriously breaks on other versions of python.
# For later versions of tensorflow there seems to be a massive overhead in the predict function for some reason, and/or it produces mysterious errors.
# Debugging these was way above my skill level.
# If the code doesn't work, make sure you are using these versions of tf and python.
# I used keras version 2.3.1, not sure if this is important, but I recommend this just to be safe.

import networkx as nx #for various graph parameters, such as eigenvalues, macthing number, etc
import random
import numpy as np
import copy
import keras
from keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Dense
from keras.optimizers import SGD, Adam
from keras.models import load_model
from statistics import mean
from math import sqrt
from numpy.random import choice
import pickle
import time
import math
import matplotlib.pyplot as plt

In [2]:
from stabilizer_search.search.brute_force import *
from stabilizer_search.mat import X, T
from stabilizer_search.mat import tensor

In [3]:
n_qubits = 3
chi = 3

In [4]:
# plus = np.array([[1/sqrt(2)], [1/sqrt(2)]], dtype=np.complex_)
# H = T*plus
H = [[np.cos(np.pi/8)],[np.sin(np.pi/8)]]
target_state = tensor(*([H]*n_qubits))
real = np.allclose(np.imag(target_state), 0.)

In [5]:
stabilizers = get_stabilizer_states(n_qubits, real_only=real)
shuffle(stabilizers)
n_stabilizers = len(stabilizers)

In [6]:
# y_true = [[0, 1, 0], [0, 0, 1]]
# y_pred = [[0.05, 0.95, 0], [0.1, 0.8, 0.1]]
# cce = keras.losses.SparseCategoricalCrossentropy()
# cce(y_true, y_pred).numpy()

In [7]:
# do_brute_force(target_state=target_state,n_qubits=3,chi=2)

In [8]:
# Daochen: would be easier if could enforce the use of combinations
# MYN = int(2**n)  #The length of the word we are generating. Here we are generating a Boolean function on n bits, so we create a 0-1 word of length 2^n

MYN = int(chi)

# LEARNING_RATE = 0.0001 #Increase this to make convergence faster, decrease if the algorithm gets stuck in local optima too often.
LEARNING_RATE = 0.0001
n_sessions =1000 #number of new sessions per iteration
# default 93, 94 respectively
percentile = 93 #top 100-X percentiled we are learning from
super_percentile = 94 #top 100-X percentile that survives to next iteration

# These are hyperparameters
FIRST_LAYER_NEURONS = 128 #Number of neurons in the hidden layers.
SECOND_LAYER_NEURONS = 64
THIRD_LAYER_NEURONS = 4

# n_actions = 2
# Daochen: note that this parameter is not actually used anywhere.
n_actions = n_stabilizers
#The size of the alphabet. In this file we will assume this is 2. There are a few things we need to change when the alphabet size is larger,
#such as one-hot encoding the input, and using categorical_crossentropy as a loss function.

observation_space = 2*MYN 

# Leave this at 2*MYN. The input vector will have size 2*MYN, 
# where the first MYN letters encode our partial word (with zeros on
# the positions we haven't considered yet), and the next MYN bits one-hot encode which letter we are considering now.
# So e.g. [0,1,0,0,   0,0,1,0] means we have the partial word 01 and we are considering the third letter now.
# Is there a better way to format the input to make it easier for the neural network to understand things?

# Daochen: why should len_game have anything to do with MYN
len_game = MYN 
state_dim = (observation_space,)

INF = 1000000

#Model structure: a sequential network with three hidden layers, sigmoid activation in the output.
#I usually used relu activation in the hidden layers but play around to see what activation function and what optimizer works best.
#It is important that the loss is binary cross-entropy if alphabet size is 2.

model = Sequential()
model.add(Dense(FIRST_LAYER_NEURONS,  activation="relu"))
model.add(Dense(SECOND_LAYER_NEURONS, activation="relu"))
model.add(Dense(THIRD_LAYER_NEURONS, activation="relu"))
model.add(Dense(n_stabilizers, activation="softmax"))
model.build((None, observation_space))
model.compile(loss="sparse_categorical_crossentropy", optimizer=SGD(learning_rate = LEARNING_RATE)) #Adam optimizer also works well, with lower learning rate

print(model.summary())

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 128)               896       
_________________________________________________________________
dense_1 (Dense)              (None, 64)                8256      
_________________________________________________________________
dense_2 (Dense)              (None, 4)                 260       
_________________________________________________________________
dense_3 (Dense)              (None, 1080)              5400      
Total params: 14,812
Trainable params: 14,812
Non-trainable params: 0
_________________________________________________________________
None


In [9]:
def calcScore(state):
    """
    Calculates the reward for a given word. 
    This function is very slow, it can be massively sped up with numba -- but numba doesn't support networkx yet, which is very convenient to use here
    :param state: the first MYN letters of this param are the word that the neural network has constructed.


    :returns: the reward (a real number). Higher is better, the network will try to maximize this.
    """

    f = state[:MYN];
    candidate_stabilizer_basis = [stabilizers[f[i]] for i in range(MYN)]
    projector = ortho_projector(candidate_stabilizer_basis)
    projection = np.linalg.norm(projector*target_state, 2)
#     projection = 1
    
    score = projection
    target = score
    
    if np.allclose(score, 1):
        print('You found a stabilizer decomposition with (n_qubits,chi) = ', [n_qubits,chi])
        print('The set of stabilizers is: ', f)
    return target, score

####No need to change anything below here. 
# Daochen: the agent argument will be the "model"
def generate_session(agent, n_sessions, verbose = 1):
    """
    Play n_session games using agent neural network.
    Terminate when games finish 

    Code inspired by https://github.com/yandexdataschool/Practical_RL/blob/master/week01_intro/deep_crossentropy_method.ipynb
    """
    states =  np.zeros([n_sessions, observation_space, len_game], dtype=int)
    actions = np.zeros([n_sessions, len_game], dtype = int)
    state_next = np.zeros([n_sessions,observation_space], dtype = int)
    prob = np.zeros(n_sessions)
    states[:,MYN,0] = 1
    step = 0
    total_target = np.zeros([n_sessions])
#     total_target = np.zeros([n_sessions], dtype=complex)
    total_score = np.zeros([n_sessions])
    recordsess_time = 0
    play_time = 0
    scorecalc_time = 0
    pred_time = 0
    while (True):
        step += 1
        tic = time.time()
        prob = agent.predict(states[:,:,step-1], batch_size = n_sessions) 
        pred_time += time.time()-tic

        for i in range(n_sessions):
            action = choice(n_stabilizers, p=prob[i])
#             print('probability vector: ', prob[i],' and action chosen: ', action)
            
#             if np.random.rand() < prob[i]:
#                 action = 1
#             else:
#                 action = 0
            actions[i][step-1] = action
            tic = time.time()
            state_next[i] = states[i,:,step-1]
            play_time += time.time()-tic
            if (action > 0):
                state_next[i][step-1] = action
            state_next[i][MYN + step-1] = 0
            if (step < MYN):
                state_next[i][MYN + step] = 1
#                 Daochen: terminal equals whether step equals MYN: I suppose meaning that an entire state has been generated
            terminal = step == MYN
            tic = time.time()
            if terminal:
#                 print('state_next[i]', state_next[i])
                total_target[i], total_score[i] = calcScore(state_next[i])
#                 print("total_score", total_score[i])
            scorecalc_time += time.time()-tic
            tic = time.time()
            if not terminal:
                states[i,:,step] = state_next[i]
            recordsess_time += time.time()-tic
        if terminal:
            break
    #If you want, print out how much time each step has taken. This is useful to find the bottleneck in the program.		
    if (verbose):
        print("Predict: "+str(pred_time)+", play: " + str(play_time) +", scorecalc: " + str(scorecalc_time) +", recordsess: " + str(recordsess_time))
    return states, actions, total_score, total_target

def select_elites(states_batch, actions_batch, rewards_batch, percentile=50):
    """
    Select states and actions from games that have rewards >= percentile
    :param states_batch: list of lists of states, states_batch[session_i][t]
    :param actions_batch: list of lists of actions, actions_batch[session_i][t]
    :param rewards_batch: list of rewards, rewards_batch[session_i]

    :returns: elite_states,elite_actions, both 1D lists of states and respective actions from elite sessions

    This function was mostly taken from https://github.com/yandexdataschool/Practical_RL/blob/master/week01_intro/deep_crossentropy_method.ipynb
    If this function is the bottleneck, it can easily be sped up using numba
    """
    counter = n_sessions * (100.0 - percentile) / 100.0
    reward_threshold = np.percentile(rewards_batch,percentile)

    elite_states = []
    elite_actions = []
    elite_rewards = []
    for i in range(len(states_batch)):
        if rewards_batch[i] >= reward_threshold-0.0000001:
            if (counter > 0) or (rewards_batch[i] >= reward_threshold+0.0000001):
                for item in states_batch[i]:
                    elite_states.append(item.tolist())
                for item in actions_batch[i]:
                    elite_actions.append(item)
            counter -= 1
    elite_states = np.array(elite_states, dtype = int)
    elite_actions = np.array(elite_actions, dtype = int)
    return elite_states, elite_actions

def select_super_sessions(states_batch, actions_batch, rewards_batch, targets_batch, percentile=90):
    """
    Select all the sessions that will survive to the next generation
    Similar to select_elites function
    If this function is the bottleneck, it can easily be sped up using numba
    """
    counter = n_sessions * (100.0 - percentile) / 100.0
    reward_threshold = np.percentile(rewards_batch,percentile)

    super_states = []
    super_actions = []
    super_rewards = []
    super_targets = []
    for i in range(len(states_batch)):
        if rewards_batch[i] >= reward_threshold-0.0000001:
            if (counter > 0) or (rewards_batch[i] >= reward_threshold+0.0000001):
                super_states.append(states_batch[i])
                super_actions.append(actions_batch[i])
                super_rewards.append(rewards_batch[i])
                super_targets.append(targets_batch[i])
                counter -= 1
    super_states = np.array(super_states, dtype = int)
    super_actions = np.array(super_actions, dtype = int)
    super_rewards = np.array(super_rewards)
    super_targets = np.array(super_targets)
    return super_states, super_actions, super_rewards, super_targets

In [10]:
super_states =  np.empty((0,len_game,observation_space), dtype = int)
super_actions = np.array([], dtype = int)
super_rewards = np.array([])
super_targets= np.array([])
sessgen_time = 0
fit_time = 0
score_time = 0

myRand = random.randint(0,1000) #used in the filename

In [ ]:
for i in range(1000000): #1000000 generations should be plenty
    #generate new sessions
    #performance can be improved with joblib
    tic = time.time()
#     sessions = states, actions, total_score, total_target
    sessions = generate_session(model,n_sessions,0) #change 0 to 1 to print out how much time each step in generate_session takes 
    sessgen_time = time.time()-tic
    tic = time.time()

    states_batch = np.array(sessions[0], dtype = int)
    actions_batch = np.array(sessions[1], dtype = int)
    rewards_batch = np.array(sessions[2])
    targets_batch = np.array(sessions[3])
    
    states_batch = np.transpose(states_batch,axes=[0,2,1])
    states_batch = np.append(states_batch,super_states,axis=0)

    if i>0:
        actions_batch = np.append(actions_batch,np.array(super_actions),axis=0)	
    
    rewards_batch = np.append(rewards_batch,super_rewards)
    targets_batch = np.append(targets_batch,super_targets)

    randomcomp_time = time.time()-tic 
    tic = time.time()

    elite_states, elite_actions = select_elites(states_batch, actions_batch, rewards_batch, percentile=percentile) #pick the sessions to learn from
    select1_time = time.time()-tic

    tic = time.time()
    super_sessions = select_super_sessions(states_batch, actions_batch, rewards_batch, targets_batch, percentile=super_percentile) #pick the sessions to survive
    select2_time = time.time()-tic

    tic = time.time()
    super_sessions = [(super_sessions[0][i], super_sessions[1][i], super_sessions[2][i], super_sessions[3][i]) for i in range(len(super_sessions[2]))]
    super_sessions.sort(key=lambda super_sessions: super_sessions[2],reverse=True)
    select3_time = time.time()-tic

    tic = time.time()
    model.fit(elite_states, elite_actions) #learn from the elite sessions
    fit_time = time.time()-tic

    tic = time.time()

    super_states = [super_sessions[i][0] for i in range(len(super_sessions))]
    super_actions = [super_sessions[i][1] for i in range(len(super_sessions))]
    super_rewards = [super_sessions[i][2] for i in range(len(super_sessions))]
    super_targets = [super_sessions[i][3] for i in range(len(super_sessions))]
    
#     print(super_states)

    rewards_batch.sort()
#     Daochen: why is it -100?
    mean_all_reward = np.mean(rewards_batch[-100:])
    mean_best_reward = np.mean(super_rewards)

    score_time = time.time()-tic

    print("\n" + str(i) +  ". Best individuals (reward): " + str(np.flip(np.sort(super_rewards))))
#     Daochen: note that sometimes it makes sense to add/remove np.flip below
    print("\n" + str(i) +  ". Best individuals (target): " + str(np.flip(np.sort(super_targets))))

    #uncomment below line to print out how much time each step in this loop takes. 
#     print("Mean reward: " + str(mean_all_reward) + "\nSessgen: " + str(sessgen_time) + ", other: " + str(randomcomp_time) + ", select1: " + str(select1_time) + ", select2: " + str(select2_time) + ", select3: " + str(select3_time) +  ", fit: " + str(fit_time) + ", score: " + str(score_time))
#     if (i%25 == 1): #Write all important info to files every 20 iterations
#         with open('best_species_pickle_'+str(myRand)+'.txt', 'wb') as fp:
#             pickle.dump(super_actions, fp)
#         with open('best_species_txt_'+str(myRand)+'.txt', 'w') as f:
#             for item in super_actions:
#                 f.write(str(item))
#                 f.write("\n")
#         with open('best_species_rewards_'+str(myRand)+'.txt', 'w') as f:
#             for item in super_rewards:
#                 f.write(str(item))
#                 f.write("\n")
#         with open('best_100_rewards_'+str(myRand)+'.txt', 'a') as f:
#             f.write(str(mean_all_reward)+"\n")
#         with open('best_elite_rewards_'+str(myRand)+'.txt', 'a') as f:
#             f.write(str(mean_best_reward)+"\n")
#     if (i%200==2): # To create a timeline, like in Figure 3
#         with open('best_species_timeline_txt_'+str(myRand)+'.txt', 'a') as f:
#             f.write(str(super_actions[0]))
#             f.write("\n")

7/7 [==============================] - 0s 2ms/step - loss: 5.3134

0. Best individuals (reward): [0.95948054 0.91229732 0.89935296 0.89372461 0.88774559 0.88063635
 0.87995338 0.8777965  0.87184289 0.86948958 0.86833639 0.86219174
 0.86085069 0.86084458 0.8602685  0.85539124 0.85213299 0.84931669
 0.84894681 0.8446232  0.83900021 0.8364401  0.83493503 0.83371609
 0.83168816 0.8291562  0.8291562  0.82748244 0.824834   0.82412472
 0.82330045 0.82282412 0.82266439 0.82080797 0.8202776  0.82022473
 0.81930589 0.81858568 0.81585522 0.81585522 0.81430475 0.81320662
 0.81223592 0.81210701 0.81067984 0.81009259 0.80677652 0.80543275
 0.80489461 0.80363756 0.80317029 0.80245497 0.80222566 0.80206348
 0.80075712 0.80075712 0.7995048  0.7995048  0.79938508 0.79938508]

0. Best individuals (target): [0.95948054 0.91229732 0.89935296 0.89372461 0.88774559 0.88063635
 0.87995338 0.8777965  0.87184289 0.86948958 0.86833639 0.86219174
 0.86085069 0.86084458 0.8602685  0.85539124 0.85213299 0.84931669


8/8 [==============================] - 0s 3ms/step - loss: 5.0199

6. Best individuals (reward): [0.95948054 0.94671378 0.93764681 0.92532925 0.92001063 0.91741819
 0.91644363 0.91612046 0.91229732 0.91143624 0.91142638 0.91128363
 0.90663291 0.90616193 0.90500585 0.90419572 0.90188045 0.90138782
 0.89989555 0.89935296 0.8974619  0.89691556 0.89661662 0.89527307
 0.89422147 0.89387886 0.89372461 0.8922994  0.89153166 0.89026395
 0.88941182 0.88941182 0.88774559 0.88774559 0.88558233 0.8851389
 0.8851389  0.8851389  0.8851389  0.88442894 0.88377939 0.88343919
 0.88342394 0.88227879 0.88134936 0.88114233 0.88063635 0.88013183
 0.87997525 0.87995338 0.87983017 0.87926988 0.87787135 0.8777965
 0.87754346 0.87647933 0.87533535 0.87533535 0.87524476 0.87491238
 0.87359087 0.87336143 0.87324105 0.8722819 ]

6. Best individuals (target): [0.95948054 0.94671378 0.93764681 0.92532925 0.92001063 0.91741819
 0.91644363 0.91612046 0.91229732 0.91143624 0.91142638 0.91128363
 0.90663291 0.90616193 0

8/8 [==============================] - 0s 3ms/step - loss: 4.6876

12. Best individuals (reward): [0.96480291 0.95948054 0.95121486 0.94832376 0.94671378 0.94348558
 0.93764681 0.93669891 0.92720022 0.92532925 0.92501202 0.92127286
 0.92001063 0.91976675 0.91834403 0.91741819 0.91709346 0.91644363
 0.91612046 0.91538429 0.9139188  0.91229732 0.91229732 0.91229732
 0.91143624 0.91142638 0.91128363 0.91128363 0.90837081 0.90794925
 0.90794925 0.90663291 0.90616193 0.90587305 0.90558408 0.90558408
 0.90511101 0.90500585 0.90474638 0.90474638 0.90442726 0.90419572
 0.90302888 0.90191857 0.90188045 0.90188045 0.90138782 0.90138782
 0.90121771 0.9005299  0.9005163  0.90021278 0.89989555 0.89935296
 0.89882069 0.89823811 0.89823811 0.89781179 0.8974619  0.89691556
 0.89691556 0.89691556 0.89691556]

12. Best individuals (target): [0.96480291 0.95948054 0.95121486 0.94832376 0.94671378 0.94348558
 0.93764681 0.93669891 0.92720022 0.92532925 0.92501202 0.92127286
 0.92001063 0.91976675 0.918344

8/8 [==============================] - 0s 3ms/step - loss: 4.5546

18. Best individuals (reward): [0.96583783 0.96480291 0.96480291 0.95948054 0.95154499 0.95121486
 0.95121486 0.94832376 0.94671378 0.94534519 0.94348558 0.93764681
 0.93669891 0.93429446 0.93278214 0.93130428 0.92765541 0.92720022
 0.92532925 0.92523836 0.92501202 0.92127286 0.92005127 0.92001063
 0.91976675 0.91834403 0.91741819 0.91709346 0.91644363 0.91612046
 0.91538429 0.9139188  0.91339501 0.91229732 0.91229732 0.91229732
 0.91229732 0.91143624 0.91142638 0.91128363 0.91128363 0.91128363
 0.91128363 0.90961797 0.9086589  0.90837081 0.90794925 0.90794925
 0.90794925 0.90663291 0.90616193 0.90587305 0.90558408 0.90558408
 0.90558408 0.90511101 0.90500585 0.90500585 0.90474638 0.90474638
 0.9047166  0.90442726 0.90419572 0.90302888]

18. Best individuals (target): [0.96583783 0.96480291 0.96480291 0.95948054 0.95154499 0.95121486
 0.95121486 0.94832376 0.94671378 0.94534519 0.94348558 0.93764681
 0.93669891 0.934294

8/8 [==============================] - 0s 10ms/step - loss: 4.4922

24. Best individuals (reward): [0.96583783 0.96480291 0.96480291 0.96480291 0.96441953 0.96236611
 0.95948054 0.95154499 0.95121486 0.95121486 0.95121486 0.94993101
 0.94832376 0.94671378 0.94671378 0.94534519 0.94348558 0.94105716
 0.93764681 0.93669891 0.93429446 0.93407033 0.93278214 0.93130428
 0.92765541 0.92765541 0.92720022 0.92720022 0.92720022 0.92720022
 0.92532925 0.92523836 0.92501202 0.92127286 0.92005127 0.92005127
 0.92001063 0.91976675 0.91834403 0.91810669 0.91741819 0.91725106
 0.91709346 0.91644363 0.91612046 0.91563549 0.91538429 0.91477754
 0.9139188  0.91339501 0.91229732 0.91229732 0.91229732 0.91229732
 0.91229732 0.91229732 0.91229732 0.91229732 0.91212292 0.91212292
 0.91143624 0.91142638]

24. Best individuals (target): [0.96583783 0.96480291 0.96480291 0.96480291 0.96441953 0.96236611
 0.95948054 0.95154499 0.95121486 0.95121486 0.95121486 0.94993101
 0.94832376 0.94671378 0.94671378 0.94534

...

8/8 [==============================] - 0s 2ms/step - loss: 2.2235

2734. Best individuals (reward): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.98152348 0.98152348 0.98152348]

2734. Best individuals (target): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99

8/8 [==============================] - 0s 3ms/step - loss: 2.2431

2740. Best individuals (reward): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492]

2740. Best individuals (target): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.991

8/8 [==============================] - 0s 3ms/step - loss: 2.2526

2746. Best individuals (reward): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.98152348 0.98152348]

2746. Best individuals (target): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99

8/8 [==============================] - 0s 3ms/step - loss: 2.2259

2752. Best individuals (reward): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.98152348 0.98152348 0.98152348 0.98152348]

2752. Best individuals (target): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99

8/8 [==============================] - 0s 3ms/step - loss: 2.2236

2758. Best individuals (reward): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.98152348 0.97215355 0.97215355 0.97215355 0.97215355
 0.97215355 0.97215355]

2758. Best individuals (target): [0.99764163 0.99192492 0.99192492 0.99192492 0.99192492 0.99192492
 0.99192492 0.99192492 0.99192492 0.99